In [1]:
import requests
from bs4 import BeautifulSoup

import pandas as pd
import numpy as np

import sys
import os
from pypdf import PdfReader
from pypdf import PdfWriter
from pathlib import Path

In [2]:
pd.set_option('display.max.columns', 7)
pd.set_option('display.max_colwidth', None)
pd.set_option('display.max.rows', 2000)
pd.set_option("display.float_format", lambda x: "%.2f" % x )

# Scraping Jumia Website

Scraping the jumia website by cateory

## Core variables

In [3]:
#The host url
host_url = "https://www.jumia.com.ng/"


categoryName = "laptops"
categoryTitle = categoryName.replace("-", " ").title()
outputFileName = categoryName.replace("-", "_")

#The host category url
host_category_url = f"{host_url}/{categoryName}"

#Total PageCount
pagesCount = 50

## Core functions

In [4]:
def loadSoup(host_url):
    #Set headers User-Agent variables for the get request
    headers = {
        'User-Agent': 'Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/97.0.4692.99 Safari/537.36'
    }
    
    try:
        # Make the HTTP GET request with the specified headers
        response = requests.get(host_url, headers=headers)
        response.raise_for_status()  # Raise an exception for bad status codes
    
        # Parse the HTML content using Beautiful Soup
        soup = BeautifulSoup(response.content, 'html.parser')
    
        # Now you can work with the 'soup' object to extract data
        # print(soup.prettify())

        return(soup)
    
    except requests.exceptions.RequestException as e:
        return(False)
        print(f"Error making request: {e}")

In [5]:
#A function that accepts the itemsList and returns a list of structured dicts
# containing 'name', 'price', 'currency', 'rating', 'link', 'img'
def loadItem(itemsList, categoryTitle):
    #the array that contains all objects
    thisItemsObjs = []

    #loop through the item list
    for thisItem in itemsList:
        #This thisItem Link
        thisItem_link = thisItem.find("a", class_="core")['href']

        #This thisItem img
        thisItem_img = thisItem.find("div", class_="img-c").find("img", class_="img")['data-src']

        #This thisItem name
        thisItem_name = thisItem.find("div", class_="info").find("h3", class_="name").text.strip()

        #This thisItem price
        thisItem_price = thisItem.find("div", class_="info").find("div", class_="prc").text.split(" ")

        #This thisItem rating
        thisItem_rating = thisItem.find("div", class_="info").find("div", class_="rev").find("div", class_="stars _s").text if (thisItem.find("div", class_="info").find("div", class_="rev")) else "No Rating"

        #Setting up this ItemObj dict
        thisItemObj = {
            "name": f"{thisItem_name}",
            "price": f"{thisItem_price[1]}".replace(",", ""),
            "currency": "NGN" if (thisItem_price[0].strip() == "₦") else "NGN",
            "rating": f"{thisItem_rating}".split(" out of ")[0],
            "link": f"{host_url}{thisItem_link}",
            "img": f"{thisItem_img}", 
            "categpry": f"{categoryTitle}"
        }
        # Append the dict to the thisItemsObjs list
        thisItemsObjs.append(thisItemObj)
    
    #return thisItemsObjs list
    return(thisItemsObjs)

## Load Items

In [7]:
#itemsObjs that hold all itemObj
itemsObjs = []

# a lost of pageLinks
pageLinks = []


#Loop through the pages
print("Loading...Please wait...")
for thisPageIdx in np.arange(pagesCount):
    #set up the page_url 
    page_url = "{}/?page={}".format(host_category_url, thisPageIdx+1) if (thisPageIdx+1 > 1) else "{}/".format(host_category_url)

    #load the soup using the loadSoup function above
    soup = loadSoup(page_url)

    #if the soup is loaded
    if (soup != False):
        #Get the itemSections
        itemSections = soup.find(class_="-pvs col12").find("div", class_="-phs -pvxs row _no-g _4cl-3cm-shs")

        #get the itemsList
        itemsList = itemSections.find_all("article")

        #load the ItemObj and append to itemsObjs
        itemsObjs.extend(loadItem(itemsList, categoryTitle))

    # THe page url obj
    page_url_obj = {}
    page_url_obj['page_url'] = page_url
    page_url_obj['items_found'] = len(itemsList)

    #Append the page url obj to the global pageLinks
    pageLinks.append(page_url_obj)


    # Completion Message
    if (thisPageIdx == pagesCount - 1): print(len(itemsObjs), " records found!", "Proceed")

Loading...Please wait...
2000  records found! Proceed


## Dataframe for the pageLinks

In [8]:
#Dataframe of the list of pageLinks extracted from
df1_pageLinks = pd.DataFrame(pageLinks)
df1_pageLinks

page_url  items_found
0           https://www.jumia.com.ng//laptops/           40
1    https://www.jumia.com.ng//laptops/?page=2           40
2    https://www.jumia.com.ng//laptops/?page=3           40
3    https://www.jumia.com.ng//laptops/?page=4           40
4    https://www.jumia.com.ng//laptops/?page=5           40
5    https://www.jumia.com.ng//laptops/?page=6           40
6    https://www.jumia.com.ng//laptops/?page=7           40
7    https://www.jumia.com.ng//laptops/?page=8           40
8    https://www.jumia.com.ng//laptops/?page=9           40
9   https://www.jumia.com.ng//laptops/?page=10           40
10  https://www.jumia.com.ng//laptops/?page=11           40
11  https://www.jumia.com.ng//laptops/?page=12           40
12  https://www.jumia.com.ng//laptops/?page=13           40
13  https://www.jumia.com.ng//laptops/?page=14           40
14  https://www.jumia.com.ng//laptops/?page=15           40
15  https://www.jumia.com.ng//laptops/?page=16           40
16  https://www.jumia.com.ng//laptops/?page=17           40
17  https://www.jumia.com.ng//laptops/?page=18           40
18  https://www.jumia.com.ng//laptops/?page=19           40
19  https://www.jumia.com.ng//laptops/?page=20           40
20  https://www.jumia.com.ng//laptops/?page=21           40
21  https://www.jumia.com.ng//laptops/?page=22           40
22  https://www.jumia.com.ng//laptops/?page=23           40
23  https://www.jumia.com.ng//laptops/?page=24           40
24  https://www.jumia.com.ng//laptops/?page=25           40
25  https://www.jumia.com.ng//laptops/?page=26           40
26  https://www.jumia.com.ng//laptops/?page=27           40
27  https://www.jumia.com.ng//laptops/?page=28           40
28  https://www.jumia.com.ng//laptops/?page=29           40
29  https://www.jumia.com.ng//laptops/?page=30           40
30  https://www.jumia.com.ng//laptops/?page=31           40
31  https://www.jumia.com.ng//laptops/?page=32           40
32  https://www.jumia.com.ng//laptops/?page=33           40
33  https://www.jumia.com.ng//laptops/?page=34           40
34  https://www.jumia.com.ng//laptops/?page=35           40
35  https://www.jumia.com.ng//laptops/?page=36           40
36  https://www.jumia.com.ng//laptops/?page=37           40
37  https://www.jumia.com.ng//laptops/?page=38           40
38  https://www.jumia.com.ng//laptops/?page=39           40
39  https://www.jumia.com.ng//laptops/?page=40           40
40  https://www.jumia.com.ng//laptops/?page=41           40
41  https://www.jumia.com.ng//laptops/?page=42           40
42  https://www.jumia.com.ng//laptops/?page=43           40
43  https://www.jumia.com.ng//laptops/?page=44           40
44  https://www.jumia.com.ng//laptops/?page=45           40
45  https://www.jumia.com.ng//laptops/?page=46           40
46  https://www.jumia.com.ng//laptops/?page=47           40
47  https://www.jumia.com.ng//laptops/?page=48           40
48  https://www.jumia.com.ng//laptops/?page=49           40
49  https://www.jumia.com.ng//laptops/?page=50           40

## Dataframe for the itemObjs

In [25]:
#Dataframe of the itemObjs
df1_itemsObjs = pd.DataFrame(itemsObjs)
df1_itemsObjs = df1_itemsObjs[['name', 'price', 'categpry', 'currency', 'rating', 'img', 'link']]
df1_itemsObjs.head()

name  \
0                            Ace Elec 14.1'' Intel(R)Pentium(R) CPU N3700 16GB+128GB - Silver   
1              Macbook PRO Laptop A1278 13.3 Inch Core I5 2.5GHz 8GB RAM 500GB EN/AR Keyboard   
2                          Blueing 15.6" Laptop J4125 8GB+256GB SSD Student Portable Computer   
3                               DELL Latitude 11  Intel Celeron 4GB RAM- 64GB HDD WIN 10+ BAG   
4  Hp Hp Hp EliteBook 840 G7 10th Gen Intel Core I5 Touchscreen 16GB RAM/512GB SSD Win 11 Pro   

    price categpry currency rating  \
0  213999  Laptops      NGN    3.6   
1  185999  Laptops      NGN    3.5   
2  234061  Laptops      NGN    3.9   
3  135000  Laptops      NGN    3.7   
4  529200  Laptops      NGN    4.1   

                                                                                           img  \
0  https://ng.jumia.is/unsafe/fit-in/300x300/filters:fill(white)/product/19/8487963/1.jpg?3957   
1  https://ng.jumia.is/unsafe/fit-in/300x300/filters:fill(white)/product/54/8858693/1.jpg?9433   
2  https://ng.jumia.is/unsafe/fit-in/300x300/filters:fill(white)/product/10/8071473/1.jpg?0416   
3  https://ng.jumia.is/unsafe/fit-in/300x300/filters:fill(white)/product/12/4395104/1.jpg?7396   
4  https://ng.jumia.is/unsafe/fit-in/300x300/filters:fill(white)/product/38/6886101/1.jpg?2059   

                                                                                                                                        link  
0                                           https://www.jumia.com.ng//ace-elec-14.1-intelrpentiumr-cpu-n3700-16gb128gb-silver-369784891.html  
1             https://www.jumia.com.ng//renewed-macbook-pro-laptop-a1278-13.3-inch-core-i5-2.5ghz-8gb-ram-500gb-enar-keyboard-396858845.html  
2                                  https://www.jumia.com.ng//blueing-15.6-laptop-j4125-8gb256gb-ssd-student-portable-computer-374170801.html  
3                                      https://www.jumia.com.ng//stream-11-pro-intel-celeron-4gb-ram-64gb-hdd-win-10-bag-hp-mpg11437537.html  
4  https://www.jumia.com.ng//elitebook-840-g6-intel-core-i5-16gb-ram512gb-ssdbacklit-keyboardfp-reader-windows-11-pro-bag-hp-mpg4091619.html

## Cleansing the df1_itemsObjs

In [26]:
df1_itemsObjs.shape

(2000, 7)

In [27]:
df1_itemsObjs_clickable = df1_itemsObjs.style.format(hyperlinks = "html")

In [35]:
df1_itemsObjs_clickable

In [36]:
df1_itemsObjs.head()

name  \
0                            Ace Elec 14.1'' Intel(R)Pentium(R) CPU N3700 16GB+128GB - Silver   
1              Macbook PRO Laptop A1278 13.3 Inch Core I5 2.5GHz 8GB RAM 500GB EN/AR Keyboard   
2                          Blueing 15.6" Laptop J4125 8GB+256GB SSD Student Portable Computer   
3                               DELL Latitude 11  Intel Celeron 4GB RAM- 64GB HDD WIN 10+ BAG   
4  Hp Hp Hp EliteBook 840 G7 10th Gen Intel Core I5 Touchscreen 16GB RAM/512GB SSD Win 11 Pro   

    price categpry currency rating  \
0  213999  Laptops      NGN    3.6   
1  185999  Laptops      NGN    3.5   
2  234061  Laptops      NGN    3.9   
3  135000  Laptops      NGN    3.7   
4  529200  Laptops      NGN    4.1   

                                                                                           img  \
0  https://ng.jumia.is/unsafe/fit-in/300x300/filters:fill(white)/product/19/8487963/1.jpg?3957   
1  https://ng.jumia.is/unsafe/fit-in/300x300/filters:fill(white)/product/54/8858693/1.jpg?9433   
2  https://ng.jumia.is/unsafe/fit-in/300x300/filters:fill(white)/product/10/8071473/1.jpg?0416   
3  https://ng.jumia.is/unsafe/fit-in/300x300/filters:fill(white)/product/12/4395104/1.jpg?7396   
4  https://ng.jumia.is/unsafe/fit-in/300x300/filters:fill(white)/product/38/6886101/1.jpg?2059   

                                                                                                                                        link  
0                                           https://www.jumia.com.ng//ace-elec-14.1-intelrpentiumr-cpu-n3700-16gb128gb-silver-369784891.html  
1             https://www.jumia.com.ng//renewed-macbook-pro-laptop-a1278-13.3-inch-core-i5-2.5ghz-8gb-ram-500gb-enar-keyboard-396858845.html  
2                                  https://www.jumia.com.ng//blueing-15.6-laptop-j4125-8gb256gb-ssd-student-portable-computer-374170801.html  
3                                      https://www.jumia.com.ng//stream-11-pro-intel-celeron-4gb-ram-64gb-hdd-win-10-bag-hp-mpg11437537.html  
4  https://www.jumia.com.ng//elitebook-840-g6-intel-core-i5-16gb-ram512gb-ssdbacklit-keyboardfp-reader-windows-11-pro-bag-hp-mpg4091619.html

In [37]:
#Check for duplicates
duplicateCount = df1_itemsObjs.duplicated().sum()
df1_itemsObjs_duplicate = False
if (duplicateCount > 0):
    #Save duplicates to a seperate dataframe
    df1_itemsObjs_duplicate = df1_itemsObjs[df1_itemsObjs.duplicated()]

    #Filter the duplicates off the main dataframe
    df1_itemsObjs = df1_itemsObjs[~df1_itemsObjs.duplicated()]
    print(duplicateCount, "Duplicate Removed!")
else: print("No Duplicate Found!")

No Duplicate Found!


In [47]:
#Check the datatype of the columns
df1_itemsObjs.dtypes

name         object
price       float64
categpry     object
currency     object
rating      float64
img          object
link         object
dtype: object

In [39]:
#Clean the rating column change no rating to 0
df1_itemsObjs['rating'] = df1_itemsObjs['rating'].apply(lambda x: x.replace("No Rating", "0"))

In [40]:
#Convert the price and rating column to float
df1_itemsObjs['price'] = df1_itemsObjs['price'].astype("float")
df1_itemsObjs['rating'] = df1_itemsObjs['rating'].astype("float")

In [41]:
df1_itemsObjs.dtypes

name         object
price       float64
categpry     object
currency     object
rating      float64
img          object
link         object
dtype: object

In [42]:
#Check for na
df1_itemsObjs.isna().sum()

name        0
price       0
categpry    0
currency    0
rating      0
img         0
link        0
dtype: int64

In [43]:
#Check for nulls
df1_itemsObjs.isnull().sum()

name        0
price       0
categpry    0
currency    0
rating      0
img         0
link        0
dtype: int64

In [44]:
df1_itemsObjs.sort_values(['price'], ascending = False)

name  \
929                                                                                                                      Asus ROG STRIX G815 (G815LW-G18.U95080) INTEL CORE ULTRA 9 32GB DDR5 RAM 2TB SSD 18" WQXGA SCREEN DISPLAY 16GB NVIDIA RTX 5080 GRAPHIC CARD   
554                                                                                                                                                                                                                          Samsung GALAXY BOOK5 PRO 360 (NP960QHA)   
1479                                                                                                                             Asus ROG ZEPHYRUS GAMING G16 14TH GEN INTEL CORE ULTRA 9 16GB RAM 1TB SSD 16"OLED NVIDIA RTX 4070 (8GB) BACKLIT KEYBOARD WINDOWS 11   
468                                                                                                                                                                           Alienware M18 R2 GAMING 14TH GEN,CORE I7-14700HX,1TB SSD/16GB RAM, RTX 4070,18" WIN 11   
848                                                                                                                              Asus ROG ZEPHYRUS GAMING G16 14TH GEN INTEL CORE ULTRA 9 16GB RAM 1TB SSD 16"OLED NVIDIA RTX 4070 (8GB) BACKLIT KEYBOARD WINDOWS 11   
1061                                                                                                                Lenovo Legion 5i 15IAX10 - 15.1" WQXGA OLED Display - 32GB RAM / 1TB SSD - Nvidia GeForce RTX 5070 (8GB) - Intel Core Ultra 7 255HX - Windows 11   
638                                                                                                                                           DELL XPS 9640 14TH GEN INTEL CORE ULTRA 7 16GB RAM 1TB SSD BACKLIT KEYBOARD NVIDIA RTX 4050 (6GB) FP READER WINDOWS 11   
895                                                                                         DELL XPS 14 9440 Intel Core Ultra 7 155H 1TB SSD 32GB 14.5" 3.2k OLED Infinity Touchscreen Display (3200 X 2000) WINDOWS 11  FP Reader,Backlit Keyboard, Platinum Silver   
368                                                                                                          Hp Omen 16 Gaming - 16GB RAM / 1TB SSD - Nvidia GeForce RTX 5060 (8GB) - Intel Core Ultra 7 255H - 16.0" 2K (1920 x 1200) IPS LED Display - Windows 11.   
843                                                                                                                                                                                                            Apple MacBook Air 15" - M4, 512 GB SSD, Silver - 2025   
1082                                                                                                                                                                                                                                              Hp Spectre x360 14   
782                                                                                                                                                           Lenovo LEGION 5 GAMING 14TH GEN INTEL CORE I7 5.2GHZ 16GB RAM 1TB SSSD RTX 4060 (8GB) 16"WQXGA WINS 11   
1038                                                           Hp EliteBook X360 830 G10 13.3" Convertible 2 In 1 Notebook Touchscreen- WUXGA - 1920 X 1200 - 13th Gen Intel Core I7-1355U Deca-core (10 Core)-Intel Evo Platform - 16 GB RAM - 512GB SSD WIN 11 PRO   
536                                                                                                                                                           Lenovo LEGION 5 GAMING 14TH GEN INTEL CORE I7 5.2GHZ 16GB RAM 1TB SSSD RTX 4060 (8GB) 16"WQXGA WINS 11   
1713                                                                                                                                                             Hp EliteBook X360 1040 G11 13.3 2-In-1 Laptop, Intel Core I7-155U 16GB RAM, 1TB SSD, Windows 11 Pro   
731                             

## Save to File

In [45]:
df1_itemsObjs.shape

(2000, 7)

In [66]:
folder_name = outputFileName
def createDfOutputFiles():
    if (df1_pageLinks is not False): 
        df1_pageLinks.to_csv(f"{folder_name}/{outputFileName}_pagelinks.csv")
        print(f"Created {outputFileName}_pagelinks.csv")
    if (df1_pageLinks is not False): 
        df1_itemsObjs.to_csv(f"{folder_name}/{outputFileName}.csv")
        print(f"Created {outputFileName}.csv")
    
osHasDir = False
if os.path.isdir(folder_name):
    osHasDir = True
else:    
    try:
        if (os.mkdir(folder_name)):
            osHasDir = True
        
    except FileExistsError:
        osHasDir = False
        print(f"Folder '{folder_name}' already exists.")

if (osHasDir == True) :
    createDfOutputFiles()

Created laptops_pagelinks.csv
Created laptops.csv
